In [1]:
!pip install transformers==4.33.0 accelerate==0.22.0 einops==0.6.1 langchain==0.0.300 xformers==0.0.21 \
bitsandbytes==0.41.1 sentence_transformers==2.2.2 chromadb==0.4.12

  Using cached transformers-4.33.0-py3-none-any.whl.metadata (119 kB)
  Using cached accelerate-0.22.0-py3-none-any.whl.metadata (17 kB)
  Using cached einops-0.6.1-py3-none-any.whl.metadata (12 kB)
  Using cached langchain-0.0.300-py3-none-any.whl.metadata (15 kB)
  Using cached xformers-0.0.21.tar.gz (22.3 MB)


ERROR: Could not install packages due to an OSError: [Errno 2] No such file or directory: 'C:\\Users\\siddi\\AppData\\Local\\Temp\\pip-install-cyo5pvb9\\xformers_0b8bc7bb638a4071b04db9b2990bef40\\third_party/flash-attention/csrc/cutlass/docs/classcutlass_1_1epilogue_1_1thread_1_1LinearCombinationRelu_3_01ElementOutput___00_01Count_00_014d4e40c4295be6a8d8778d86e94fe14a.html'
HINT: This error might have occurred since this system does not have Windows Long Path support enabled. You can find information on how to enable this at https://pip.pypa.io/warnings/enable-long-paths



In [2]:
from torch import cuda, bfloat16
import torch
import transformers
from transformers import AutoTokenizer
from time import time
#import chromadb
#from chromadb.config import Settings
from langchain.llms import HuggingFacePipeline
from langchain.document_loaders import TextLoader
from langchain.text_splitter import RecursiveCharacterTextSplitter
from langchain.embeddings import HuggingFaceEmbeddings
from langchain.chains import RetrievalQA
from langchain.vectorstores import Chroma
from langchain import PromptTemplate, LLMChain

In [3]:
pip install -q accelerate bitsandbytes


Note: you may need to restart the kernel to use updated packages.


In [4]:
model_id = '/kaggle/input/llama-2/pytorch/7b-chat-hf/1'

device = f'cuda:{cuda.current_device()}' if cuda.is_available() else 'cpu'

# set quantization configuration to load large model with less GPU memory
# this requires the `bitsandbytes` library
bnb_config = transformers.BitsAndBytesConfig(
    load_in_4bit=True,
    bnb_4bit_quant_type='nf4',
    bnb_4bit_use_double_quant=True,
    bnb_4bit_compute_dtype=bfloat16
)

In [5]:
time_1 = time()
model_config = transformers.AutoConfig.from_pretrained(
    model_id,
)
model = transformers.AutoModelForCausalLM.from_pretrained(
    model_id,
    trust_remote_code=True,
    config=model_config,
    quantization_config=bnb_config,
    device_map='auto',
)
tokenizer = AutoTokenizer.from_pretrained(model_id)
time_2 = time()
print(f"Prepare model, tokenizer: {round(time_2-time_1, 3)} sec.")

2024-05-20 11:26:12.744027: E external/local_xla/xla/stream_executor/cuda/cuda_dnn.cc:9261] Unable to register cuDNN factory: Attempting to register factory for plugin cuDNN when one has already been registered
2024-05-20 11:26:12.744143: E external/local_xla/xla/stream_executor/cuda/cuda_fft.cc:607] Unable to register cuFFT factory: Attempting to register factory for plugin cuFFT when one has already been registered
2024-05-20 11:26:12.880595: E external/local_xla/xla/stream_executor/cuda/cuda_blas.cc:1515] Unable to register cuBLAS factory: Attempting to register factory for plugin cuBLAS when one has already been registered


Loading checkpoint shards:   0%|          | 0/2 [00:00<?, ?it/s]

/opt/conda/lib/python3.10/site-packages/transformers/generation/configuration_utils.py:362: UserWarning: `do_sample` is set to `False`. However, `temperature` is set to `0.9` -- this flag is only used in sample-based generation modes. You should set `do_sample=True` or unset `temperature`. This was detected when initializing the generation config instance, which means the corresponding file may hold incorrect parameterization and should be fixed.
  warnings.warn(
/opt/conda/lib/python3.10/site-packages/transformers/generation/configuration_utils.py:367: UserWarning: `do_sample` is set to `False`. However, `top_p` is set to `0.6` -- this flag is only used in sample-based generation modes. You should set `do_sample=True` or unset `top_p`. This was detected when initializing the generation config instance, which means the corresponding file may hold incorrect parameterization and should be fixed.
  warnings.warn(


Prepare model, tokenizer: 181.376 sec.


In [6]:
time_1 = time()
summarization_pipeline = transformers.pipeline(
        "text-generation",
        model=model,
        tokenizer=tokenizer,
        torch_dtype=torch.float16,
        trust_remote_code=True,
        device_map="auto",)
time_2 = time()
print(f"Prepare pipeline: {round(time_2-time_1, 3)} sec.")

Prepare pipeline: 1.569 sec.


In [7]:
llm = HuggingFacePipeline(pipeline=summarization_pipeline, model_kwargs={'temperature': 0})

template = """
Write a concise summary of the following text in bullet points:
'''{text}'''
SUMMARY:

"""

prompt = PromptTemplate(template=template, input_variables=["text"])

llm_chain = LLMChain(prompt=prompt, llm=llm)

In [8]:
def test_model(text):
    """
    This function summarizes a given text string and returns a bulleted list of key points.
    Args:
        text: The text string to be summarized.
    Returns:
        A string containing the bulleted list summary of the text, or None if there's an error.
    """
    time_1 = time()
    summary = llm_chain.run(text=text)
    time_2 = time()
    print(f"Test inference: {round(time_2-time_1, 3)} sec.")
    print(f"Summary: {summary}")

In [9]:
test_model("Artificial intelligence (AI) is a branch of computer science focused on developing intelligent machines that can mimic human cognitive functions like learning, problem-solving, anddecision-making. AI research has made significant progress in recent years, with advancementsin machine learning algorithms and the increasing availability of data. AI applications are nowwidespread, impacting various sectors like healthcare, finance, transportation, and manufacturing.From medical diagnosis tools to self-driving cars, AI is transforming industries and raisingethical considerations regarding automation, bias, and human control. As AI continues to evolve,it's crucial to develop responsible AI practices that ensure its benefits are harnessed for thebetterment of society.")

/opt/conda/lib/python3.10/site-packages/transformers/generation/utils.py:1417: UserWarning: You have modified the pretrained model configuration to control generation. This is a deprecated strategy to control generation and will be removed soon, in a future version. Please use a generation configuration file (see https://huggingface.co/docs/transformers/main_classes/text_generation )
  warnings.warn(


Test inference: 8.968 sec.
Summary: • AI is a branch of computer science focused on developing intelligent machines.
• AI research has made significant progress in recent years.
• AI applications are now widespread and impact various sectors.
• AI raises ethical considerations regarding automation, bias, and human control.
• It's crucial to develop responsible AI practices to ensure benefits for society.


In [10]:
with open('/kaggle/input/testing-dataset/thyroid.txt', "r") as f:
            extracted_text = f.read()
text = extracted_text
test_model(text)

Test inference: 25.157 sec.
Summary: * Hyperthyroidism occurs when the thyroid gland produces too much thyroid hormone, leading to symptoms such as weight loss, rapid heartbeat, and anxiety.
* Hypothyroidism occurs when the thyroid gland produces too little thyroid hormone, leading to symptoms such as fatigue, weight gain, and cold sensitivity.
* The pituitary gland plays a crucial role in regulating thyroid hormone production by producing thyroid-stimulating hormone (TSH).
* Disorders related to the pituitary gland include hypopituitarism, hyperpituitarism, and pituitary tumors.
* There are three types of hypothyroidism: primary, secondary, and compensated.
* Lithium can have effects on the thyroid gland, including hypothyroidism and goitre.
* The Free Thyroxine Index (FTI) is a calculated value used to estimate the level of free thyroxine (T4) in the blood.








In [11]:
pip install pdfminer.six

huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 5.6/5.6 MB 49.3 MB/s eta 0:00:0000:0100:01
Note: you may need to restart the kernel to use updated packages.


In [12]:
!pip install PyPdf2

huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 232.6/232.6 kB 5.2 MB/s eta 0:00:00a 0:00:01


In [13]:
from PyPDF2 import PdfReader
pdfreader = PdfReader('/kaggle/input/ai-dataset/ai.pdf')

In [14]:
from typing_extensions import Concatenate
text = ""
for i,page in enumerate(pdfreader.pages):
    content = page.extract_text()
    if content:
        text += content

In [15]:
from langchain.docstore.document import Document 

In [16]:
docs = [Document(page_content=text)]

In [17]:
text_splitter = RecursiveCharacterTextSplitter(chunk_size=1000, chunk_overlap=20)
chunks = text_splitter.create_documents([text])

In [18]:
len(chunks)

40

loader = TextLoader("/kaggle/input/testing-dataset/thyroid.txt",
                    encoding="utf8")
documents = loader.load()

In [19]:
model_name = "sentence-transformers/all-mpnet-base-v2"
model_kwargs = {"device": "cuda"}

embeddings = HuggingFaceEmbeddings(model_name=model_name, model_kwargs=model_kwargs)

.gitattributes:   0%|          | 0.00/1.23k [00:00<?, ?B/s]

1_Pooling/config.json:   0%|          | 0.00/190 [00:00<?, ?B/s]

README.md:   0%|          | 0.00/10.6k [00:00<?, ?B/s]

config.json:   0%|          | 0.00/571 [00:00<?, ?B/s]

config_sentence_transformers.json:   0%|          | 0.00/116 [00:00<?, ?B/s]

...

tokenizer.json:   0%|          | 0.00/466k [00:00<?, ?B/s]

tokenizer_config.json:   0%|          | 0.00/363 [00:00<?, ?B/s]

train_script.py:   0%|          | 0.00/13.1k [00:00<?, ?B/s]

vocab.txt:   0%|          | 0.00/232k [00:00<?, ?B/s]

modules.json:   0%|          | 0.00/349 [00:00<?, ?B/s]

In [20]:
vectordb = Chroma.from_documents(documents=chunks, embedding=embeddings, persist_directory="chroma_db")

Batches:   0%|          | 0/2 [00:00<?, ?it/s]

In [21]:
retriever = vectordb.as_retriever()

In [22]:
qa = RetrievalQA.from_chain_type(
    llm=llm, 
    chain_type="stuff", 
    retriever=retriever, 
    verbose=True
)

In [23]:
def test_rag(qa, **kwargs):
    print(f"Query: {kwargs['query']}\n")
    time_1 = time()
    result = qa.run(**kwargs)
    time_2 = time()
    print(f"Inference time: {round(time_2-time_1, 3)} sec.")

    if isinstance(result, list):
        print("\nResult: ", result[0]['summary_text'])
    else:
        print("\nResult: ", result)

In [24]:
test_rag(qa, query="Can you summarize this long piece of text into a concise summary in not more than 300 words?", 
         num_outputs=1, max_length=300, min_length=30, do_sample=False)

Query: Can you summarize this long piece of text into a concise summary in not more than 300 words?



> Entering new RetrievalQA chain...


Batches:   0%|          | 0/1 [00:00<?, ?it/s]


> Finished chain.
Inference time: 19.592 sec.

Result:   Sure, here is a summary of the text in 300 words or less:

The text discusses the history and evolution of artificial intelligence (AI) and its impact on society. AI can be classified into different types, such as analytical, human-inspired, and humanized AI, depending on its cognitive, emotional, and social intelligence. The author argues that when AI reaches mainstream usage, it is frequently no longer considered as such, and this phenomenon is known as the AI effect. The text also mentions that advances in AI have led to the development of image recognition, smart speakers, and self-driving cars, and it has entered the business environment and public conversation. The author concludes that AI has the potential to revolutionize many aspects of our lives, but it also raises important ethical and societal questions that need to be addressed.


In [25]:
test_rag(qa, query="Can you summarize this long piece of text into a concise summary in not more than 500 words?", 
         num_outputs=1, max_length=500, min_length=30, do_sample=False)

Query: Can you summarize this long piece of text into a concise summary in not more than 500 words?



> Entering new RetrievalQA chain...


Batches:   0%|          | 0/1 [00:00<?, ?it/s]


> Finished chain.
Inference time: 35.34 sec.

Result:   Of course! Here is a summary of the text in 475 words:

The article discusses the history and future of artificial intelligence (AI). The author divides AI's history into four seasons: spring, summer, fall, and winter. Spring represents the birth of AI, summer its growth and development, fall its challenges and limitations, and winter its potential future advancements.

In the spring season, AI was born out of the need to automate tasks and solve complex problems. The first AI program was developed in the 1950s, and since then, AI has evolved rapidly, with the development of new algorithms, models, and techniques. Summer represents the growth and development of AI, where it became more sophisticated and capable of performing a wide range of tasks.

In the fall season, AI faced challenges and limitations, such as the lack of data, the difficulty of interpreting results, and the need for better integration with human systems. Despi